# Cascading Impacts Analysis: 2023 Turkey-Syria Earthquake

This notebook demonstrates how to use the **Montandon STAC API** to analyze a major natural disaster and its cascading impacts. 

**Scenario**: The magnitude 7.8 earthquake that struck Turkey and Syria on February 6, 2023.

**Workflow**:
1.  **Primary Event**: Find the main earthquake event using hazard codes (`GH0101`, `EQ`, `nat-geo-ear-gro`, etc.).
2.  **Secondary Hazards**: Identify triggered hazards:
    *   **Aftershocks** (`GH0101`)
    *   **Landslides** (`LS`, `nat-hyd-mmw-lan`, `nat-geo-mmd-lan`)
3.  **Cascading Impacts**: Retrieve impact data (displacement, damages) for the affected countries (`TUR`, `SYR`).
4.  **Visualization**: Map the event sequence and impacts.

**Data Sources**:
-   Events/Hazards: USGS, GDACS, EM-DAT
-   Impacts: IDMC, EM-DAT

In [52]:
# Import required libraries
import pystac_client
import pandas as pd
import geopandas as gpd
import folium
from datetime import datetime, timedelta
import json

# Set API URL
STAC_API_URL = "https://montandon-eoapi-stage.ifrc.org/stac"

# Connect to the client
client = pystac_client.Client.open(STAC_API_URL)
print(f"Connected to {STAC_API_URL}")

Connected to https://montandon-eoapi-stage.ifrc.org/stac


## 1. Find the Primary Event (Earthquake)

We search for the major earthquake on **February 6, 2023**, using a comprehensive list of hazard codes.

In [53]:
# Define earthquake hazard codes
EARTHQUAKE_HAZARD_CODES = [
    "GH0101",           # UNDRR-ISC 2025: Earthquake (Seismic cluster)
    "EQ",               # GLIDE
    "nat-geo-ear-gro",  # EM-DAT: Earthquake > Ground movement
    "GH0001",           # UNDRR-ISC 2020: Earthquake
    "GH0002",           # UNDRR-ISC 2020: Ground Shaking
]

# Define search parameters
target_date = "2023-02-06"
start_datetime = f"{target_date}T00:00:00Z"
end_datetime = f"{target_date}T23:59:59Z"

# Helper function to extract magnitude from various sources
def get_magnitude(item):
    """Extract magnitude from eq:magnitude or monty:hazard_detail.severity_value"""
    # Try eq:magnitude first (USGS, GDACS)
    mag = item.properties.get("eq:magnitude")
    if mag is not None:
        return mag
    
    # Try monty:hazard_detail.severity_value (Monty extension)
    hazard_detail = item.properties.get("monty:hazard_detail")
    if hazard_detail and isinstance(hazard_detail, dict):
        mag = hazard_detail.get("severity_value")
        if mag is not None:
            return mag
    
    return None  # Return None if no magnitude found (we'll filter these out)



## 2. Find Secondary Hazards (Aftershocks & Landslides)

We search for:
1.  **Aftershocks**: Subsequent earthquakes (`GH0101`) in the days following the main event.
2.  **Landslides**: Mass movements triggered by the shaking (`LS`, `nat-geo-mmd-lan`, etc.).

In [54]:
# Define search window for secondary hazards (e.g., 5 days after)
event_time = pd.to_datetime(main_event.datetime)
aftershock_start = event_time + timedelta(minutes=10)
aftershock_end = event_time + timedelta(days=5)

print(f"Searching for secondary hazards between {aftershock_start} and {aftershock_end}...")

# --- 2a. Aftershocks ---
# Search USGS hazards (no filter needed)
usgs_aftershock_search = client.search(
    collections=["usgs-hazards"],
    datetime=f"{aftershock_start.isoformat()}/{aftershock_end.isoformat()}",
    limit=500
)
usgs_aftershocks = list(usgs_aftershock_search.items())

Searching for secondary hazards between 2023-02-06 01:27:34.342000+00:00 and 2023-02-11 01:17:34.342000+00:00...


In [55]:
# Search GDACS hazards (with filter)
aftershock_filter = {
    "op": "and",
    "args": [
        {
            "op": "or",
            "args": hazard_code_filters # Reuse earthquake codes
        },
        {
            "op": "t_intersects",
            "args": [{"property": "datetime"}, {"interval": [aftershock_start.isoformat(), aftershock_end.isoformat()]}]
        }
    ]
}

gdacs_aftershock_search = client.search(
    collections=["gdacs-hazards"],
    filter=aftershock_filter,
    filter_lang="cql2-json",
    limit=500
)
gdacs_aftershocks = list(gdacs_aftershock_search.items())

aftershocks = usgs_aftershocks + gdacs_aftershocks
print(f"Found {len(aftershocks)} aftershocks.")

# --- 2b. Landslides ---
LANDSLIDE_HAZARD_CODES = [
    "GH0007",           # UNDRR-ISC 2020: Landslide (Earthquake Trigger)
    "GH0301",           # UNDRR-ISC 2025: Landslide
    "LS",               # GLIDE
    "nat-hyd-mmw-lan",  # EM-DAT: Hydrological > Mass movement (wet) > Landslide
    "nat-geo-mmd-lan"   # EM-DAT: Geophysical > Mass movement (dry) > Landslide
]

landslide_code_filters = [{"op": "a_contains", "args": [{"property": "monty:hazard_codes"}, code]} for code in LANDSLIDE_HAZARD_CODES]

landslide_filter = {
    "op": "and",
    "args": [
        {
            "op": "or",
            "args": landslide_code_filters
        },
        {
            "op": "t_intersects",
            "args": [{"property": "datetime"}, {"interval": [aftershock_start.isoformat(), aftershock_end.isoformat()]}]
        }
    ]
}

search_landslides = client.search(
    collections=["usgs-hazards", "gdacs-hazards", "emdat-hazards"],
    filter=landslide_filter,
    filter_lang="cql2-json",
    limit=100
)
landslides = list(search_landslides.items())
print(f"Found {len(landslides)} landslides.")

Found 2306 aftershocks.
Found 1 landslides.


In [56]:
# Search USGS hazards (ShakeMap products contain eq:magnitude data)
print("\nSearching USGS hazards (ShakeMap products)...")
usgs_search = client.search(
    collections=["usgs-hazards"],
    datetime=f"{start_datetime}/{end_datetime}",
    limit=50
)
usgs_hazards = list(usgs_search.items())
print(f"Found {len(usgs_hazards)} USGS hazards")

# Build filter for GDACS and EMDAT (they use monty:hazard_codes)
hazard_code_filters = [{"op": "a_contains", "args": [{"property": "monty:hazard_codes"}, code]} for code in EARTHQUAKE_HAZARD_CODES]

primary_event_filter = {
    "op": "and",
    "args": [
        {
            "op": "or",
            "args": hazard_code_filters
        },
        {
            "op": "t_intersects",
            "args": [{"property": "datetime"}, {"interval": [start_datetime, end_datetime]}]
        }
    ]
}

# Search GDACS and EMDAT with hazard code filters
print("Searching GDACS and EMDAT events...")
gdacs_emdat_search = client.search(
    collections=["gdacs-events", "emdat-events"],
    filter=primary_event_filter,
    filter_lang="cql2-json",
    limit=20
)
gdacs_emdat_events = list(gdacs_emdat_search.items())
print(f"Found {len(gdacs_emdat_events)} GDACS/EMDAT events")

# Combine all events
primary_events = usgs_hazards + gdacs_emdat_events
print(f"\nTotal events found: {len(primary_events)}")

# Display found events with magnitude
print("\nAll events with magnitudes:")
events_with_mag = []
for item in primary_events:
    mag = get_magnitude(item)
    if mag is not None and mag > 0:  # Only include events with valid magnitudes
        events_with_mag.append(item)
        print(f"ID: {item.id} | Time: {item.datetime} | Mag: {mag} | Title: {item.properties.get('title')}")

if not events_with_mag:
    print("WARNING: No events with magnitude found! Using all events...")
    events_with_mag = primary_events
    # Display all events even without magnitude
    for item in primary_events:
        mag = get_magnitude(item) or 0
        print(f"ID: {item.id} | Time: {item.datetime} | Mag: {mag} | Title: {item.properties.get('title')}")




Searching USGS hazards (ShakeMap products)...
Found 515 USGS hazards
Searching GDACS and EMDAT events...
Found 6 GDACS/EMDAT events

Total events found: 521

All events with magnitudes:
ID: usgs-hazard-us6000jnv7-shakemap | Time: 2023-02-06 23:51:38.972000+00:00 | Mag: 4.6 | Title: M 4.6 - south of the Fiji Islands
ID: usgs-hazard-tx2023cpph-shakemap | Time: 2023-02-06 23:50:07.074000+00:00 | Mag: 1.9 | Title: M 1.9 - 15 km N of Balmorhea, Texas
ID: usgs-hazard-uu60530251-shakemap | Time: 2023-02-06 23:41:54.920000+00:00 | Mag: 0.24 | Title: M 0.2 - 17 km NE of West Yellowstone, Montana
ID: usgs-hazard-ak0231pks83b-shakemap | Time: 2023-02-06 23:35:01.376000+00:00 | Mag: 1.9 | Title: M 1.9 - 60 km NE of Pedro Bay, Alaska
ID: usgs-hazard-ci40411672-shakemap | Time: 2023-02-06 23:32:41.200000+00:00 | Mag: 1.84 | Title: M 1.8 - 18km NE of Olancha, CA
ID: usgs-hazard-us6000jm3x-shakemap | Time: 2023-02-06 23:29:14.993000+00:00 | Mag: 4.5 | Title: M 4.5 - 39 km WNW of Latakia, Syria
ID: us

In [57]:
# Select the event with the highest magnitude
main_event = max(events_with_mag, key=lambda x: get_magnitude(x) or 0)
main_magnitude = get_magnitude(main_event) or 0

print(f"\nSelected Primary Event: {main_event.id} ({main_event.properties.get('title')})")
print(f"Magnitude: {main_magnitude}")
print(f"Correlation ID: {main_event.properties.get('monty:correlation_id')}")

# Also extract additional earthquake details
eq_depth = main_event.properties.get("eq:depth")
eq_alert = main_event.properties.get("eq:alert")
eq_tsunami = main_event.properties.get("eq:tsunami")
print(f"Depth: {eq_depth} km" if eq_depth else "Depth: N/A")
print(f"Alert Level: {eq_alert}" if eq_alert else "Alert Level: N/A")
print(f"Tsunami: {'Yes' if eq_tsunami == 1 else 'No' if eq_tsunami == 0 else 'N/A'}")


Selected Primary Event: usgs-hazard-us6000jllz-shakemap (M 7.8 - Pazarcik earthquake, Kahramanmaras earthquake sequence)
Magnitude: 7.8
Correlation ID: None
Depth: 10.0 km
Alert Level: N/A
Tsunami: No


## 3. Find Cascading Impacts (Displacement & Damages)

We search for impact records in **Turkey (`TUR`)** and **Syria (`SYR`)**.

In [58]:
# Impact search window
impact_end = event_time + timedelta(days=30)

impact_filter = {
    "op": "and",
    "args": [
        # Filter by Country Codes
        {
            "op": "or",
            "args": [
                {"op": "a_contains", "args": [{"property": "monty:country_codes"}, "TUR"]},
                {"op": "a_contains", "args": [{"property": "monty:country_codes"}, "SYR"]}
            ]
        },
        # Filter by Time
        {
            "op": "t_intersects",
            "args": [{"property": "datetime"}, {"interval": [start_datetime, impact_end.isoformat()]}]
        }
    ]
}

print("Searching for impacts in Turkey and Syria...")
search_impacts = client.search(
    collections=["idmc-idu-impacts", "emdat-impacts", "gdacs-impacts"],
    filter=impact_filter,
    filter_lang="cql2-json",
    limit=100
)

impacts = list(search_impacts.items())
print(f"Found {len(impacts)} impact records.")

Searching for impacts in Turkey and Syria...
Found 122 impact records.


## 4. Visualization

We'll create an interactive map showing:
1.  **Main Event**: Large Red Marker
2.  **Aftershocks**: Smaller Orange Circles
3.  **Landslides**: Green Markers
4.  **Impacts**: Blue Markers

In [61]:

# Helper to get coordinates from geometry (Point or Polygon)
def get_event_coordinates(item):
    if not item.geometry:
        return None
        
    geom_type = item.geometry.get("type")
    coords = item.geometry.get("coordinates")
    
    if not coords:
        return None
        
    if geom_type == "Point":
        return coords
    elif geom_type == "Polygon":
        # Calculate centroid of the polygon (simple average of outer ring)
        try:
            outer_ring = coords[0]
            lons = [p[0] for p in outer_ring]
            lats = [p[1] for p in outer_ring]
            centroid_lon = sum(lons) / len(lons)
            centroid_lat = sum(lats) / len(lats)
            return [centroid_lon, centroid_lat]
        except (IndexError, TypeError):
            return None
    return None

In [62]:
# Helper function to add simulated intensity contours
def add_intensity_contours(map_obj, coords, magnitude):
    # Define zones (Color, Radius Multiplier in km)
    zones = [
        ("red", 40),      # Severe Shaking
        ("orange", 80),   # Strong Shaking
        ("yellow", 160)   # Moderate Shaking
    ]
    
    # Adjust radii based on magnitude relative to M7.0
    # Ensure a minimum scale to avoid tiny circles for smaller major events
    scale_factor = max(magnitude / 7.0, 0.5)
    
    for color, base_radius in zones:
        radius_km = base_radius * scale_factor
        folium.Circle(
            location=[coords[1], coords[0]],
            radius=radius_km * 1000,  # Meters
            color=color,
            weight=2,
            fill=True,
            fill_color=color,
            fill_opacity=0.15, # Slightly more transparent to handle overlap
            popup=f"Simulated Intensity Zone (~{int(radius_km)} km) for M{magnitude}"
        ).add_to(map_obj)


In [63]:
# Initialize Map centered on the main event
main_coords = get_event_coordinates(main_event)

if main_coords:
    # Folium uses [lat, lon]
    m = folium.Map(location=[main_coords[1], main_coords[0]], zoom_start=6)
    
    # Add contours for Main Event
    add_intensity_contours(m, main_coords, main_magnitude)
        
else:
    print("Warning: Could not determine main event coordinates. Defaulting to Turkey.")
    m = folium.Map(location=[37.0, 37.0], zoom_start=6)

# Create a detailed popup for the main event
main_popup_html = f"""<div style='width: 200px'>
<b>Main Earthquake Event</b><br>
<b>Magnitude:</b> {main_magnitude}<br>
<b>Date:</b> {main_event.datetime}<br>
<b>Depth:</b> {eq_depth if eq_depth else 'N/A'} km<br>
<b>Alert:</b> {eq_alert if eq_alert else 'N/A'}<br>
<b>Tsunami:</b> {'Yes' if eq_tsunami == 1 else 'No' if eq_tsunami == 0 else 'N/A'}<br>
<b>ID:</b> {main_event.id}
</div>"""

# Add Main Event Marker
if main_coords:
    folium.Marker(
        [main_coords[1], main_coords[0]],
        popup=folium.Popup(main_popup_html, max_width=250),
        tooltip=f"Main Event - Magnitude {main_magnitude}",
        icon=folium.Icon(color="red", icon="star")
    ).add_to(m)

# Initialize counters
major_event_count = 0
aftershock_count = 0

# Add Aftershocks and Major Events
print("Processing aftershocks...")
for item in aftershocks:
    coords = get_event_coordinates(item)
    if coords:
        mag = get_magnitude(item)
        if mag is None:
            continue
            
        # Check for Major Event (e.g., M >= 7.0)
        if mag >= 7.0:
            major_event_count += 1
            
            # Add Marker
            popup_html = f"""<div style='width: 150px'>
            <b>Major Event</b><br>
            <b>Magnitude:</b> {mag}<br>
            <b>Date:</b> {item.datetime}
            </div>"""
            
            folium.Marker(
                [coords[1], coords[0]],
                popup=folium.Popup(popup_html, max_width=200),
                tooltip=f"Major Event - Mag {mag}",
                icon=folium.Icon(color="red", icon="star")
            ).add_to(m)
            
            # Add Contours for Major Event
            add_intensity_contours(m, coords, mag)
            
        else:
            aftershock_count += 1
            popup_html = f"""<div style='width: 150px'>
            <b>Aftershock</b><br>
            <b>Magnitude:</b> {mag}<br>
            <b>Date:</b> {item.datetime}
            </div>"""
            
            folium.CircleMarker(
                [coords[1], coords[0]],
                radius=max(mag * 1.5, 3),  # Size by magnitude, min 3
                color="orange",
                fill=True,
                fill_opacity=0.6,
                popup=folium.Popup(popup_html, max_width=200),
                tooltip=f"Aftershock - Mag {mag}"
            ).add_to(m)

print(f"Visualization updated: Showing {major_event_count} major events (M>=7.0) and {aftershock_count} aftershocks.")

# Add Landslides
for item in landslides:
    coords = get_event_coordinates(item)
    if coords:
        popup_html = f"""<div style='width: 150px'>
        <b>Landslide</b><br>
        <b>Date:</b> {item.datetime}<br>
        <b>Location:</b> {item.properties.get('title', 'N/A')}
        </div>"""
        
        folium.Marker(
            [coords[1], coords[0]],
            popup=folium.Popup(popup_html, max_width=200),
            tooltip="Landslide",
            icon=folium.Icon(color="green", icon="leaf")
        ).add_to(m)

# Add Impacts
for item in impacts:
    coords = get_event_coordinates(item)
    if coords:
        detail = item.properties.get("monty:impact_detail", {})
        
        impact_type = detail.get('type', 'Unknown')
        impact_value = detail.get('value', 'N/A')
        impact_unit = detail.get('unit', '')
        
        popup_html = f"""<div style='width: 150px'>
        <b>Impact</b><br>
        <b>Type:</b> {impact_type}<br>
        <b>Value:</b> {impact_value} {impact_unit}
        </div>"""
        
        folium.Marker(
            [coords[1], coords[0]],
            popup=folium.Popup(popup_html, max_width=200),
            tooltip=f"{impact_type}: {impact_value} {impact_unit}",
            icon=folium.Icon(color="blue", icon="info-sign")
        ).add_to(m)

# Add a legend
legend_html = '''<div style="position: fixed; 
                 bottom: 50px; right: 50px; width: 220px; height: auto; 
                 background-color: white; z-index:9999; font-size:14px;
                 border:2px solid grey; border-radius: 5px; padding: 10px">
                 <p style="margin-bottom: 5px;"><b>Legend</b></p>
                 <p style="margin: 3px;"><span style="color: red;">★</span> Main/Major Event (M7+)</p>
                 <p style="margin: 3px;"><span style="color: red; opacity: 0.5;">●</span> Severe Shaking Zone</p>
                 <p style="margin: 3px;"><span style="color: orange; opacity: 0.5;">●</span> Strong Shaking Zone</p>
                 <p style="margin: 3px;"><span style="color: yellow; opacity: 0.5;">●</span> Moderate Shaking Zone</p>
                 <p style="margin: 3px;"><span style="color: orange;">●</span> Aftershocks</p>
                 <p style="margin: 3px;"><span style="color: green;">🍃</span> Landslides</p>
                 <p style="margin: 3px;"><span style="color: blue;">ⓘ</span> Impacts</p>
                 </div>'''




Processing aftershocks...
Visualization updated: Showing 1 major events (M>=7.0) and 2305 aftershocks.


In [64]:
m.get_root().html.add_child(folium.Element(legend_html))

# Display Map
m